# Projeto: Será que Machine Learning pode quebrar a banca? #

<p align="center">
  <img src="pexels-photo-3279691.jpg" >
</p>

Blackjack é um dos jogos mais simples que você pode jogar em um Casino.
As regras são simples, você joga contra a banca e ambos começam com duas cartas, a soma destas cartas precisa ser abaixo ou igual a 21, sendo que se você tiver 21 ganha e acima você "estoura" e automaticamente perde.
Para começar um projeto de Machine Learning preciso criar um jogo de Blackjack em python e simular um jogador usando diferentes estratégias de jogo.
Este projeto vai ficar mais complexo com o tempo, adicionando mais de um jogador, mistura de estratégias, apostas e finalmente a construção de um modelo de ML que vai jogar do melhor jeito possível de acordo com as cartas na mesa e a estratégia adotada.
Também vou analisar os dados explorando as variáveis relacioandas ao jogo, como quantidade de baralhos em nosso deck, quantidade de jogadores, etc...

Primeiro, precisamos programar o jogo:

Fazendo as funções do jogo:

In [1]:
import pandas as pd
import numpy as np
import random

#Checa a mão somando os valores e dá como output o valor da soma
def sum_hand(hand):
    d_val = {'2': 2, '3': 3, '4': 4, '5': 5,
     '6': 6, '7': 7, '8': 8, '9': 9, '10': 10,
     'J': 10, 'Q': 10, 'K': 10, 'A': 11, 'A.': 1}

    soma = sum(d_val[str(k)] for k in hand)
    return soma
#Cria o nosso "shoe", que é o baralho que vai ser utilizado
def create_shoe(n_decks=6):
    deck = [2,3,4,5,6,7,8,9,10,'J','Q','K','A']
    shoe = deck*4*n_decks
    random.shuffle(shoe)
    return shoe

#Função de comprar cartas
def deal_cards(hand,shoe,n_cards=1):
    for i in range(n_cards):
        hand.append(shoe.pop())
    return hand

#Checa se você estourou ou automaticamente ganhou
def check_hand(hand):
    if sum_hand(hand) > 21:
        hand = ace_of_spades(hand)
        if sum_hand(hand) > 21:
            return 'bust'
        else:
            return 'keep'
    elif sum_hand(hand) == 21:
        return 'win'
    else:
        return 'keep'

#Imprime os resultados, somente para conferencia
def print_results(d_hand,p_hand):
    print('\n Mão da banca: ', d_hand,' valendo',sum_hand(d_hand), ' pontos.' '\n Sua mão:', p_hand , ' valendo', sum_hand(p_hand) , ' pontos')

#Se você estoura e tiver um Ás na mão este Ás vale 1 ao invés de 11
def ace_of_spades(hand):
    if sum_hand(hand) > 21 and 'A' in hand:
        hand[hand.index('A')] = 'A.'
    return hand

def count_cards(p_hand,d_hand,strategy,r_count):
    r_count += card_counter(p_hand,strategy)
    r_count += card_counter(d_hand,strategy)
    return r_count




Código para contagem de cartas com oito estratégias de contagem de cartas:
Hi-Lo
Hi-opt I
Hi-Opt II
KO
Omega II
Red 7
Halves
Zen Count
Sem estratégia

In [2]:
import pandas as pd
#Fazer um dataframe com a contagem de cada carta de acordo com a estratégia
vals = {'2': 1, '3': 1, '4': 1, '5': 1, '6': 1, 
            '7': 0, '8': 0, '9': 0, '10': -1, 'J': -1, 
            'Q': -1, 'K': -1, 'A': -1, 'A.':-1}

df = pd.DataFrame(vals, index=[0])

df.loc[len(df), :] = [0,1,1,1,1,0,0,0,-1,-1,-1,-1,0,0]
df.loc[len(df), :] = [1,1,2,2,1,1,0,0,-2,-2,-2,-2,0,0]
df.loc[len(df), :] = [1,1,1,1,1,1,0,0,-1,-1,-1,-1,-1,-1]
df.loc[len(df), :] = [1,1,2,2,2,1,0,-1,-2,-2,-2,-2,0,0]
df.loc[len(df), :] = [1,1,1,1,1,0,0,0,-1,-1,-1,-1,-1,-1]
df.loc[len(df), :] = [.5,1,1,1.5,1,.5,0,-.5,-1,-1,-1,-1,-1,-1]
df.loc[len(df), :] = [1,1,2,2,2,1,0,0,-2,-2,-2,-2,-1,-1]
df.loc[len(df), :] = [0,0,0,0,0,0,0,0,0,0,0,0,0,0]

df.rename({0: 'Hi-Lo',
           1: 'Hi-Opt I',
           2: 'Hi-Opt II',
           3: 'KO',
           4: 'Omega II',
           5: 'Red 7',
           6: 'Halves',
           7: 'Zen Count',
           8: 'No Strategy'}, inplace=True)

#Para uso posterior vamos usar pickle
df.to_pickle('Card_Counting_Values')

# Conta as cartas de uma mão
def card_counter(hand, strategy='Hi-Lo'):
    
    df = pd.read_pickle('Card_Counting_Values')
    card_sum = sum([df.loc[strategy][str(i)].item() for i in hand])
    return card_sum
    
# Função recursiva que pergunta ao jogador se deseja comprar uma carta ou continuar com a mão
def ask_input(d_hand,p_hand,shoe,r_count,strategy):
    print("\nQual será sua jogada? (Hit ou Stay)")

    jogada = player_move(p_hand,15,r_count,d_hand)

    if jogada == 'hit':
        p_hand = deal_cards(p_hand,shoe,1)

        if check_hand(p_hand) == 'bust':
            print('Você estourou a mão...')
            print_results(d_hand,p_hand)
            r_count = count_cards(p_hand,d_hand,strategy,r_count)
            return ['loss',p_hand,d_hand,r_count,strategy]

        elif check_hand(p_hand) == 'win':
    
            print('21! você ganhou!')
            print_results(d_hand,p_hand)
            r_count = count_cards(p_hand,d_hand,strategy,r_count)
            return ['win', p_hand, d_hand, r_count,strategy]

        elif check_hand(p_hand) == 'keep':
            
            return ask_input(d_hand,p_hand,shoe,r_count,strategy)
            
    if jogada == 'stay':
       
        return dealer_turn(p_hand, d_hand, r_count, shoe, strategy)
    

Algoritmo de jogador, define como o jogador jogará.

In [3]:
def player_move(your_hand, limit, true_cnt, dealer_hand):
    """
    Chooses 'hit' or 'stay' depending on the limit set and count
    """
    
    dtotal = sum_hand(dealer_hand[:1])

    # Se tiver bastante cartas boas, se arrisca mais
    if true_cnt > 0:
        if sum_hand(your_hand) >= limit:
            return 'stay'
        elif sum_hand(your_hand) < limit:
            return 'hit'
        elif dtotal >= 10:
            return 'stay'
        
        
    # Cartas ruins, vai ser mais convervador
    elif true_cnt < 0:
        if sum_hand(your_hand) <= limit:
            return 'hit'
        elif sum_hand(your_hand) > limit:
            return 'stay'
        elif dtotal < 10:
            return 'hit'
        
        
    # Neutro, jogar uma estratégia genérica    
    else:
        if sum_hand(your_hand) >= 17:
            return 'stay'
        elif sum_hand(your_hand) < 17:
            return 'hit'

Algoritmo da banca

In [4]:
def dealer_turn(p_hand, d_hand, r_count, shoe, strategy): 
   
   #Ativado no turno da banca, a banca joga e checa o resultado do jogo
    if sum_hand(d_hand) > sum_hand(p_hand):
        print('A banca ganhou...')
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        print_results(d_hand,p_hand)
        return ['loss', p_hand, d_hand, r_count, strategy]
        
    elif sum_hand(d_hand) < sum_hand(p_hand) and sum_hand(d_hand) >=17 :
        print('Você ganhou!')
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        print_results(d_hand,p_hand)
        return ['win', p_hand, d_hand, r_count, strategy]

    elif sum_hand(d_hand) == sum_hand(p_hand) and sum_hand(d_hand) >= 17 :
        print('Empate! Mesma pontuação.')
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        print_results(d_hand,p_hand)
        return ['draw', p_hand, d_hand, r_count,strategy]
    
    elif sum_hand(d_hand) <= sum_hand(p_hand) and sum_hand(d_hand) < 17 :
        while sum_hand(d_hand) < 17:
            d_hand = deal_cards(d_hand,shoe,1)
            if check_hand(d_hand) == 'bust':
                print('Você venceu! A banca estourou.')
                r_count = count_cards(p_hand,d_hand,strategy,r_count)
                print_results(d_hand,p_hand)
                return ['win', p_hand, d_hand, r_count,strategy]

            elif sum_hand(d_hand) > sum_hand(p_hand):
                print('A banca ganhou...')
                r_count = count_cards(p_hand,d_hand,strategy,r_count)
                print_results(d_hand,p_hand)
                return ['loss', p_hand, d_hand, r_count,strategy]

            elif sum_hand(d_hand) == sum_hand(p_hand):
                print('Empate! Ambos tem a mesma pontuação.')
                r_count = count_cards(p_hand,d_hand,strategy,r_count)
                print_results(d_hand,p_hand)
                return ['draw', p_hand, d_hand, r_count,strategy]
            
            elif sum_hand(d_hand) < sum_hand(p_hand):
                print('O jogador ganhou!')
                r_count = count_cards(p_hand,d_hand,strategy,r_count)
                print_results(d_hand,p_hand)
                return ['win', p_hand, d_hand, r_count,strategy]

    

Algoritmo do jogo

In [5]:
def blackjack(shoe,r_count,strategy):
    
    p_hand = []
    d_hand = []
    p_hand = deal_cards(p_hand,shoe,2)
    d_hand = deal_cards(d_hand,shoe,2)
    
    if check_hand(d_hand) == 'win':
        print("\n A banca ganha com um Blackjack na primeira!")
        print_results(d_hand,p_hand)
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        return ['loss',p_hand,d_hand,r_count,strategy]

    elif check_hand(p_hand) == 'win': 
        print("\n O jogador ganha com um Blackjack na primeira!")
        print_results(d_hand,p_hand)
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        return ['win', p_hand, d_hand, r_count,strategy]

    elif check_hand(p_hand) == 'win' and check_hand(d_hand) == 'win':
        print('Um empate! Dois Blackjack de primeira!')
        print_results(d_hand,p_hand)
        r_count = count_cards(p_hand,d_hand,strategy,r_count)
        return ['draw',p_hand,d_hand,r_count,strategy]

    return ask_input(d_hand, p_hand, shoe, r_count, strategy)

Executando diferentes estratégias no jogo.
10000 turnos para cada estratégia

In [6]:
f = open('data.csv','w')
f.write('w or l,p_hand,d_hand,r_count\n')

strats = list(pd.read_pickle('Card_Counting_Values').index)

for strategy in strats:
    i = 0
    r_count = 0
    shoe = create_shoe()
    while i <10000:
        if len(shoe) <= 52:
            shoe=create_shoe()
            r_count = 0
        out = blackjack(shoe,r_count, strategy)
        r_count = out[3]
        f.write(str(out))
        f.write('\n')
        i += 1
f.close()

exit()

#df.rename({0: 'Hi-Lo',
#           1: 'Hi-Opt I',
 #          2: 'Hi-Opt II',
 #          3: 'KO',
#           4: 'Omega II',
 #          5: 'Red 7',
  #         6: 'Halves',
 #          7: 'Zen Count',
 #          8: 'No Strategy'}, inplace=True)


Qual será sua jogada? (Hit ou Stay)
O jogador ganhou!

 Mão da banca:  [5, 5, 3]  valendo 13  pontos.
 Sua mão: ['Q', 7]  valendo 17  pontos

Qual será sua jogada? (Hit ou Stay)
Você estourou a mão...

 Mão da banca:  ['K', 9]  valendo 19  pontos.
 Sua mão: [3, 'Q', 'Q']  valendo 23  pontos

Qual será sua jogada? (Hit ou Stay)
O jogador ganhou!

 Mão da banca:  [2, 9, 4]  valendo 15  pontos.
 Sua mão: [10, 'Q']  valendo 20  pontos

Qual será sua jogada? (Hit ou Stay)
21! você ganhou!

 Mão da banca:  [5, 'J']  valendo 15  pontos.
 Sua mão: [7, 4, 'J']  valendo 21  pontos

Qual será sua jogada? (Hit ou Stay)

Qual será sua jogada? (Hit ou Stay)
Você venceu! A banca estourou.

 Mão da banca:  [4, 9, 'Q']  valendo 23  pontos.
 Sua mão: [4, 6, 9]  valendo 19  pontos

Qual será sua jogada? (Hit ou Stay)

Qual será sua jogada? (Hit ou Stay)
Você venceu! A banca estourou.

 Mão da banca:  ['K', 4, 9]  valendo 23  pontos.
 Sua mão: [4, 4, 8]  valendo 16  pontos

Qual será sua jogada? (Hit ou 